# Land cover classification at the Lower Left Hand Creek Watershed in Colorado

In this notebook, you will use a k-means **unsupervised** clustering
algorithm to group pixels by similar spectral signatures. **k-means** is
an **exploratory** method for finding patterns in data. Because it is
unsupervised, you don’t need any training data for the model. You also
can’t measure how well it “performs” because the clusters will not
correspond to any particular land cover class. However, we expect at
least some of the clusters to be identifiable as different types of land
cover.

You will use the [harmonized Sentinal/Landsat multispectral
dataset](https://lpdaac.usgs.gov/documents/1698/HLS_User_Guide_V2.pdf).
You can access the data with an [Earthdata
account](https://www.earthdata.nasa.gov/learn/get-started) and the
[`earthaccess` library from
NSIDC](https://github.com/nsidc/earthaccess):

## STEP 1: SET UP

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Import all libraries you will need for this analysis</li>
<li>Configure GDAL parameters to help avoid connection errors:
<code>python      os.environ["GDAL_HTTP_MAX_RETRY"] = "5"      os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"</code></li>
</ol></div></div>

In [81]:
import os
import pathlib
import pickle
import re
import warnings

import cartopy.crs as ccrs
import earthaccess
import earthpy as et
import geopandas as gpd
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import numpy as np
import pandas as pd
import rioxarray as rxr
import rioxarray.merge as rxrmerge
from tqdm.notebook import tqdm
import xarray as xr
from shapely.geometry import Polygon
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score ### calculate silhouette score
import zipfile

os.environ["GDAL_HTTP_MAX_RETRY"] = "5"
os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"

warnings.simplefilter('ignore')

Below you can find code for a caching **decorator** which you can use in
your code. To use the decorator:

``` python
@cached(key, override)
def do_something(*args, **kwargs):
    ...
    return item_to_cache
```

This decorator will **pickle** the results of running the
`do_something()` function, and only run the code if the results don’t
already exist. To override the caching, for example temporarily after
making changes to your code, set `override=True`. Note that to use the
caching decorator, you must write your own function to perform each
task!

In [2]:
def cached(func_key, override=True):
    """
    A decorator to cache function results
    
    Parameters
    ==========
    key: str
      File basename used to save pickled results
    override: bool
      When True, re-compute even if the results are already stored
    """
    def compute_and_cache_decorator(compute_function):
        """
        Wrap the caching function
        
        Parameters
        ==========
        compute_function: function
          The function to run and cache results
        """
        def compute_and_cache(*args, **kwargs):
            """
            Perform a computation and cache, or load cached result.
            
            Parameters
            ==========
            args
              Positional arguments for the compute function
            kwargs
              Keyword arguments for the compute function
            """
            # Add an identifier from the particular function call
            if 'cache_key' in kwargs:
                key = '_'.join((func_key, kwargs['cache_key']))
            else:
                key = func_key

            path = os.path.join(
                et.io.HOME, et.io.DATA_NAME, 'jars', f'{key}.pickle')
            
            # Check if the cache exists already or override caching
            if not os.path.exists(path) or override:
                # Make jars directory if needed
                os.makedirs(os.path.dirname(path), exist_ok=True)
                
                # Run the compute function as the user did
                result = compute_function(*args, **kwargs)
                
                # Pickle the object
                with open(path, 'wb') as file:
                    pickle.dump(result, file)
            else:
                # Unpickle the object
                with open(path, 'rb') as file:
                    result = pickle.load(file)
                    
            return result
        
        return compute_and_cache
    
    return compute_and_cache_decorator

## STEP 2: STUDY SITE

For this analysis, you will use a watershed from the [Water Boundary
Dataset](https://www.usgs.gov/national-hydrography/access-national-hydrography-products),
HU12 watersheds (WBDHU12.shp).

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">You will:</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Download the Water Boundary Dataset for the Missouri region, region 10</li>
<li>Select watershed 1101900050304</li>
<li>Generate a site map of the watershed</li>
</ol>
<p>Try to use the <strong>caching decorator</strong></p></div></div>

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-response"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div></div><div class="callout-body-container callout-body"><p>Write a 2-3 sentence <strong>site description</strong> (with
citations) of this area that helps to put your analysis in context.</p></div></div>

**SEE SITE DESCRIPTION BELOW SITE MAP**

* Helpful links:

    * How's My Waterway? for the Lower Left Hand Creek watershed: https://mywaterway.epa.gov/community/101900050304/overview

    * Breakdown of all watershed boundaries including boundary descriptions, names of regions, subretions, accounting units, and cataloging units: https://water.usgs.gov/GIS/huc_name.html

    * Documentation for et.data.get_data: https://earthpy.readthedocs.io/en/latest/gallery_vignettes/get_data.html

    * Documentation for .dissolve(): https://geopandas.org/en/stable/docs/user_guide/aggregation_with_dissolve.html

<span style="color: purple;">

#### STEP 2a. Download watershed boundary data for region 10

</span>

In [3]:
# call cached decorator
@cached('wbd-10-co')
# add function to apply decorator abilities to
def read_wbd_file(wbd_filename, huc_level, cache_key):
    # Define wbd_url
    wbd_url = (
        "https://prd-tnm.s3.amazonaws.com"
        "/StagedProducts/Hydrography/WBD/HU2/Shape/"
        f"{wbd_filename}.zip")
    # et.data.get_data from earthpy library to download data from a zip file
    # can also download Earthpy Dataset Subsets w/ et.data.get_data 
    wbd_dir = et.data.get_data(url=wbd_url)
                  
    # Read desired data
    wbd_path = os.path.join(wbd_dir, 'Shape', f'WBDHU{huc_level}.shp')
    # engine is the library used to read the file
    wbd_gdf = gpd.read_file(wbd_path, engine='pyogrio')
    return wbd_gdf

# define huc_level
huc_level = 12

# create wbd_total_gdf 
co_wbd_total_gdf = read_wbd_file(
    # filename found from URL noted above code cell
    wbd_filename = 'WBD_10_HU2_Shape',
    # huc_level defined above
    huc_level = huc_level,
    # cache_key is a kwarg for cached decorator
    cache_key=f'hu{huc_level}'
)

# check wbd_total_gdf
co_wbd_total_gdf.head()


tnmid  \
0  {7BA1DB26-DE43-4C0D-AA9E-F1BCDCA73056}   
1  {BEBF876B-3038-49F5-AC50-924E64EC9D01}   
2  {9FBE3BFA-1C84-4D99-B915-1542A14E4097}   
3  {A05E4DCF-564A-4C5C-A657-D05FCD3F800A}   
4  {3E02DEF8-97FD-4D22-91F8-85F1507D8835}   

                               metasource                        sourcedata  \
0  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   
1  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   
2  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   
3  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   
4  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   

                                          sourceorig sourcefeat   loaddate  \
0  Natural Resources and Conservation Service and...       None 2024-08-15   
1  Natural Resources and Conservation Service and...       None 2024-08-15   
2  Natural Resources and Conservation Service and...       None 2024-08-15   
3  Natural Resources and Conservation Service and...       None 2024-08-15   
4  Natural Resources and Conservation Service and...       None 2024-08-15   

        referenceg  areaacres  areasqkm states  ...  \
0    778951,787781   15739.64     63.70     MT  ...   
1    828806,830826   36671.18    148.40     NE  ...   
2    800152,771632   35019.92    141.72     MT  ...   
3          1266881   18475.14     74.77     SD  ...   
4  1259556,1266881   20667.78     83.64     SD  ...   

                           name hutype humod         tohuc noncontrib  \
0        Alkali Creek-Mud Creek      S    ID  100402010107        0.0   
1  Dry Creek-Logan Creek Dredge      S    TF  102200030805        0.0   
2   Peck Coulee-Frenchman Creek      S    NM  100500131405        0.0   
3    101301051801-Okobojo Creek      S    NM  101301051802        0.0   
4   D Trumble Dam-Okobojo Creek      S    NM  101301051806        0.0   

   noncontr_1  shape_Leng  shape_Area  ObjectID  \
0         0.0         NaN         NaN         1   
1         0.0         NaN         NaN         2   
2         0.0         NaN         NaN         3   
3         0.0         NaN         NaN         4   
4         0.0         NaN         NaN         5   

                                            geometry  
0  POLYGON ((-110.32755 46.58466, -110.32759 46.5...  
1  POLYGON ((-96.53684 41.81158, -96.53605 41.811...  
2  POLYGON ((-107.38547 48.96991, -107.38174 48.9...  
3  POLYGON ((-99.88327 44.94747, -99.88327 44.947...  
4  POLYGON ((-100.21868 44.70657, -100.21872 44.7...  

[5 rows x 21 columns]

<span style="color: purple;">

#### STEP 2b. Select watershed of interest from region 10, 101900050304

</span>

In [4]:
# see all column names of the wbd_total_gdf
co_wbd_total_gdf.columns

Index(['tnmid', 'metasource', 'sourcedata', 'sourceorig', 'sourcefeat',
       'loaddate', 'referenceg', 'areaacres', 'areasqkm', 'states', 'huc12',
       'name', 'hutype', 'humod', 'tohuc', 'noncontrib', 'noncontr_1',
       'shape_Leng', 'shape_Area', 'ObjectID', 'geometry'],
      dtype='object')

In [5]:
# select the 101900050304 waterhsed rows from the wbd_total_gdf
wbd_gdf = (
    # from the huc12 column...
    co_wbd_total_gdf[co_wbd_total_gdf[f'huc{huc_level}']
    # select only the rows for 101900050304
    .isin(['101900050304'])]
    # dissolve all geometries to a single geometric feature
    # and aggreagate all rows of data in a group
    .dissolve()
)

# check wbd_gdf
wbd_gdf

geometry  \
0  POLYGON ((-105.11231 40.1368, -105.11231 40.13...   

                                    tnmid  \
0  {1E3BDF99-0F60-4BD5-B872-7E37D2E89345}   

                               metasource                        sourcedata  \
0  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   

                                          sourceorig sourcefeat   loaddate  \
0  Natural Resources and Conservation Service and...       None 2024-08-15   

  referenceg  areaacres  areasqkm  ...         huc12                   name  \
0     178283    9495.52     38.43  ...  101900050304  Lower Left Hand Creek   

  hutype     humod         tohuc noncontrib  noncontr_1  shape_Leng  \
0      S  RS,LE,TF  101900050706        0.0         0.0         NaN   

   shape_Area  ObjectID  
0         NaN      5594  

[1 rows x 21 columns]

In [8]:
print(f"Watershed {wbd_gdf['huc12']} is in {wbd_gdf['states']}")

Watershed 0    101900050304
Name: huc12, dtype: object is in 0    CO
Name: states, dtype: object


<span style="color: purple;">

#### STEP 2c. Create site map of watershed 101900050304 in Colorado, USA & describe watershed

</span>

In [9]:
# create site map with hvplot
(
    wbd_gdf
    .hvplot(
        # geographic plot, lat/lon axes
        geo=True,
        # overlay plot on EsriImagery tiles
        tiles='EsriImagery',
        # fill color
        color='white',
        # transparency of fill color
        alpha=0.4,
        # line color
        line_color='darkblue',
        line_width=4, 
        # define title
        title='Lower Left Hand Creek Watershed (101900050304) Boundary in Colorado, USA',
        # define size of plot
        frame_width=650
    )
)

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

<span style="color: maroon;">

**Site Description:**

Watershed 101900050304 is in Boulder County, Colorado. It is part of the Missouri Region which includes the United Staes drainage of the Missouri River and Saskatchewan River basins as well as some small closed basins. Nebraska is in region 10 and so are parts of Colorado, Iowa, Kansas, Minnesota, Missouri, Montana, North Dakota, South Dakota, and Wyoming. Watershed 101900050304 is in subregion 1019 which is the South Platte River Basin. Cataloging unit 10190005 is St. Vrain in Colorado.<sup>1</sup> Watershed 1019000503034 is called the Lower Left Hand Creek watershed and covers 9,496 acres. Look at the map of the watershed on How's My Waterway, we can see that part of Left Hand Creek runs west to east in this watershed. Left Hand Creek begins outside of the west side of watershed 101900050304, flows through the watershed, and then joins the St. Vrain Creek at the northeast tip of the watershed. There are is a lake in the Lower Left Hand Creek Watershed, Allens Lake, and a reservoir, Dodd Reservoir.<sup>2</sup>

**Data Description:**

The Watershed Boundary Dataset includes national hydrologic units. Hydrologic units are "an area of the landscape that drains to a portion of the stream network."<sup>3</sup>

**Citations:**

1. “Boundary Descriptions and Names of Regions, Subregions, Accounting Units and Cataloging Units from the 1987 USGS Water-Supply Paper 2294.” USGS Water Resources: About USGS Water Resources, water.usgs.gov/GIS/huc_name.html. Accessed 2 Mar. 2025. 

2. “How’s My Waterway?” EPA, Environmental Protection Agency, mywaterway.epa.gov/community/101900050304/overview. Accessed 2 Mar. 2025. 

3. “Watershed Boundary Dataset.” USGS, National Hydrography, www.usgs.gov/national-hydrography/watershed-boundary-dataset. Accessed 2 Mar. 2025. 


</span>

## STEP 3: MULTISPECTRAL DATA

### Search for data

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Log in to the <code>earthaccess</code> service using your Earthdata
credentials:
<code>python      earthaccess.login(persist=True)</code></li>
<li>Modify the following sample code to search for granules of the
HLSL30 product overlapping the watershed boundary from May to October
2023 (there should be 76 granules):
<code>python      results = earthaccess.search_data(          short_name="...",          cloud_hosted=True,          bounding_box=tuple(gdf.total_bounds),          temporal=("...", "..."),      )</code></li>
</ol></div></div>

<span style="color: maroon;">


HLSL30 data description from the NASA worldview site:

"The Harmonized Landsat Sentinel-2 (HLS) project brings us 30 meter resolution true color surface reflectance imagery from the Operational Land Imager (OLI) instrument aboard the NASA/USGS Landsat 8 and 9 satellites, and the Multi-Spectral Instrument (MSI) aboard the European Space Agency (ESA) Sentinel-2A and Sentinel-2B satellites."

MSI data citation: 

Masek, J., Ju, J., Roger, J., Skakun, S., Vermote, E., Claverie, M., Dungan, J., Yin, Z., Freitag, B., Justice, C. (2021). <i>HLS Sentinel-2 Multi-spectral Instrument Surface Reflectance Daily Global 30m v2.0</i> [Data set]. NASA EOSDIS Land Processes Distributed Active Archive Center. Accessed 2025-03-03 from https://doi.org/10.5067/HLS/HLSS30.002

OLI data citation: 

Masek, J., Ju, J., Roger, J., Skakun, S., Vermote, E., Claverie, M., Dungan, J., Yin, Z., Freitag, B., Justice, C. (2021). <i>HLS Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0</i> [Data set]. NASA EOSDIS Land Processes Distributed Active Archive Center. Accessed 2025-03-03 from https://doi.org/10.5067/HLS/HLSL30.002

</span>

<span style="color: purple;">

#### STEP 3a. Log in to EarthAccess and search for HLS tiles covering watershed 101900050304

</span>

In [10]:
# Log in to earthaccess
earthaccess.login(strategy="interactive", persist=True)

In [11]:
# Search for HLS tiles
wbd_hls_results = earthaccess.search_data(
    # dataset short name
    short_name='HLSL30',
    cloud_hosted=True,
    # the bounding box is the waterhsed boundary
    bounding_box=tuple(wbd_gdf.total_bounds),
    # temporal bounds from May - Oct 2023
    temporal=('2023-05-01', '2023-10-31')
)
wbd_hls_results


[Collection: {'EntryTitle': 'HLS Landsat Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0'}
 Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -105.60875359, 'Latitude': 39.66001162}, {'Longitude': -104.88622009, 'Latitude': 39.66155123}, {'Longitude': -104.88455693, 'Latitude': 40.65079881}, {'Longitude': -105.31427288, 'Latitude': 40.65042886}, {'Longitude': -105.60875359, 'Latitude': 39.66001162}]}}]}}}
 Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2023-05-01T17:36:46.126Z', 'EndingDateTime': '2023-05-01T17:37:10.008Z'}}
 Size(MB): 88.30738544464111
 Data: ['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B04.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B06.tif', 'https://da

In [12]:
# add the wbd_hls_results go a geodataframe
wbd_hls_gdf = gpd.GeoDataFrame(wbd_hls_results)
wbd_hls_gdf

meta  \
0   {'concept-type': 'granule', 'concept-id': 'G26...   
1   {'concept-type': 'granule', 'concept-id': 'G26...   
2   {'concept-type': 'granule', 'concept-id': 'G26...   
3   {'concept-type': 'granule', 'concept-id': 'G26...   
4   {'concept-type': 'granule', 'concept-id': 'G26...   
5   {'concept-type': 'granule', 'concept-id': 'G26...   
6   {'concept-type': 'granule', 'concept-id': 'G26...   
7   {'concept-type': 'granule', 'concept-id': 'G27...   
8   {'concept-type': 'granule', 'concept-id': 'G27...   
9   {'concept-type': 'granule', 'concept-id': 'G27...   
10  {'concept-type': 'granule', 'concept-id': 'G27...   
11  {'concept-type': 'granule', 'concept-id': 'G27...   
12  {'concept-type': 'granule', 'concept-id': 'G27...   
13  {'concept-type': 'granule', 'concept-id': 'G27...   
14  {'concept-type': 'granule', 'concept-id': 'G27...   
15  {'concept-type': 'granule', 'concept-id': 'G27...   
16  {'concept-type': 'granule', 'concept-id': 'G27...   
17  {'concept-type': 'granule', 'concept-id': 'G27...   
18  {'concept-type': 'granule', 'concept-id': 'G27...   
19  {'concept-type': 'granule', 'concept-id': 'G27...   
20  {'concept-type': 'granule', 'concept-id': 'G27...   
21  {'concept-type': 'granule', 'concept-id': 'G27...   
22  {'concept-type': 'granule', 'concept-id': 'G27...   
23  {'concept-type': 'granule', 'concept-id': 'G27...   
24  {'concept-type': 'granule', 'concept-id': 'G27...   
25  {'concept-type': 'granule', 'concept-id': 'G27...   
26  {'concept-type': 'granule', 'concept-id': 'G27...   
27  {'concept-type': 'granule', 'concept-id': 'G27...   
28  {'concept-type': 'granule', 'concept-id': 'G27...   
29  {'concept-type': 'granule', 'concept-id': 'G27...   
30  {'concept-type': 'granule', 'concept-id': 'G27...   
31  {'concept-type': 'granule', 'concept-id': 'G27...   
32  {'concept-type': 'granule', 'concept-id': 'G27...   
33  {'concept-type': 'granule', 'concept-id': 'G27...   
34  {'concept-type': 'granule', 'concept-id': 'G27...   
35  {'concept-type': 'granule', 'concept-id': 'G27...   
36  {'concept-type': 'granule', 'concept-id': 'G27...   
37  {'concept-type': 'granule', 'concept-id': 'G27...   
38  {'concept-type': 'granule', 'concept-id': 'G27...   
39  {'concept-type': 'granule', 'concept-id': 'G27...   
40  {'concept-type': 'granule', 'concept-id': 'G27...   
41  {'concept-type': 'granule', 'concept-id': 'G27...   
42  {'concept-type': 'granule', 'concept-id': 'G27...   
43  {'concept-type': 'granule', 'concept-id': 'G27...   
44  {'concept-type': 'granule', 'concept-id': 'G27...   

                                                  umm        size  
0   {'TemporalExtent': {'RangeDateTime': {'Beginni...   88.307385  
1   {'TemporalExtent': {'RangeDateTime': {'Beginni...  208.793959  
2   {'TemporalExtent': {'RangeDateTime': {'Beginni...   87.973766  
3   {'TemporalExtent': {'RangeDateTime': {'Beginni...  206.257804  
4   {'TemporalExtent': {'RangeDateTime': {'Beginni...   88.950211  
5   {'TemporalExtent': {'RangeDateTime': {'Beginni...  196.662627  
6   {'TemporalExtent': {'RangeDateTime': {'Beginni...   86.096684  
7   {'TemporalExtent': {'RangeDateTime': {'Beginni...  207.117194  
8   {'TemporalExtent': {'RangeDateTime': {'Beginni...   86.472710  
9   {'TemporalExtent': {'RangeDateTime': {'Beginni...  203.631255  
10  {'TemporalExtent': {'RangeDateTime': {'Beginni...   94.803090  
11  {'TemporalExtent': {'RangeDateTime': {'Beginni...  200.675011  
12  {'TemporalExtent': {'RangeDateTime': {'Beginni...   82.866386  
13  {'TemporalExtent': {'RangeDateTime': {'Beginni...  189.016415  
14  {'TemporalExtent': {'RangeDateTime': {'Beginni...   79.448449  
15  {'TemporalExtent': {'RangeDateTime': {'Beginni...  186.979414  
16  {'TemporalExtent': {'RangeDateTime': {'Beginni...   85.573983  
17  {'TemporalExtent': {'RangeDateTime': {'Beginni...  186.536498  
18  {'TemporalExtent': {'RangeDateTime': {'Beginni...   84.524065  
19  {'TemporalExtent': {'RangeDateTime': {'Beginni...  207.798252 

### Compile information about each granule

I recommend building a GeoDataFrame, as this will allow you to plot the
granules you are downloading and make sure they line up with your
shapefile. You could also use a DataFrame, dictionary, or a custom
object to store this information.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each search result:
<ol type="1">
<li>Get the following information (HINT: look at the [‘umm’] values for
each search result):
<ul>
<li>granule id (UR)</li>
<li>datetime</li>
<li>geometry (HINT: check out the shapely.geometry.Polygon class to
convert points to a Polygon)</li>
</ul></li>
<li>Open the granule files. I recomment opening one granule at a time,
e.g. with (<code>earthaccess.open([result]</code>).</li>
<li>For each file (band), get the following information:
<ul>
<li>file handler returned from <code>earthaccess.open()</code></li>
<li>tile id</li>
<li>band number</li>
</ul></li>
</ol></li>
<li>Compile all the information you collected into a GeoDataFrame</li>
</ol></div></div>

<span style="color: purple;">

#### STEP 3b. Explore HLS data before building granule metadata GeoDataFrame

</span>

In [13]:
# look at the 'umm' column for the first row
wbd_hls_gdf['umm'].loc[0]

{'TemporalExtent': {'RangeDateTime': {'BeginningDateTime': '2023-05-01T17:36:46.126Z',
   'EndingDateTime': '2023-05-01T17:37:10.008Z'}},
 'GranuleUR': 'HLS.L30.T13TDE.2023121T173646.v2.0',
 'AdditionalAttributes': [{'Name': 'LANDSAT_PRODUCT_ID',
   'Values': ['LC08_L1TP_033032_20230501_20230501_02_RT',
    'LC08_L1TP_033033_20230501_20230501_02_RT']},
  {'Name': 'CLOUD_COVERAGE', 'Values': ['14']},
  {'Name': 'MGRS_TILE_ID', 'Values': ['13TDE']},
  {'Name': 'SPATIAL_COVERAGE', 'Values': ['45']},
  {'Name': 'SPATIAL_RESOLUTION', 'Values': ['30.0']},
  {'Name': 'SPATIAL_RESAMPLING_ALG', 'Values': ['Cubic Convolution']},
  {'Name': 'HLS_PROCESSING_TIME', 'Values': ['2023-05-03T06:35:09Z']},
  {'Name': 'SENSING_TIME',
   'Values': ['2023-05-01T17:36:46.1260500Z', '2023-05-01T17:37:10.0086180Z']},
  {'Name': 'HORIZONTAL_CS_NAME',
   'Values': ['UTM, WGS84, UTM ZONE 13', 'UTM, WGS84, UTM ZONE 13']},
  {'Name': 'ULX', 'Values': ['399960.0']},
  {'Name': 'ULY', 'Values': ['4500000.0']},
  {'N

In [14]:
# isolate the granule ID (UR) for the first row
row1 = list(wbd_hls_gdf['umm'].loc[0].values())
row1[1]

'HLS.L30.T13TDE.2023121T173646.v2.0'

In [15]:
# isolate the datetime for the first row
row1[0]

{'RangeDateTime': {'BeginningDateTime': '2023-05-01T17:36:46.126Z',
  'EndingDateTime': '2023-05-01T17:37:10.008Z'}}

In [16]:
# identify the keys for the first row
# the geometry, 'SpatialExtent' key is index 3
row1_keys = list(wbd_hls_gdf['umm'].loc[0].keys())
row1_keys

['TemporalExtent',
 'GranuleUR',
 'AdditionalAttributes',
 'SpatialExtent',
 'ProviderDates',
 'CollectionReference',
 'RelatedUrls',
 'DataGranule',
 'Platforms',
 'MetadataSpecification']

In [17]:
# isolate the SpatialExtent for the first row
# this is a dictionary
spatialextent = row1[3]
spatialextent

{'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -105.60875359,
        'Latitude': 39.66001162},
       {'Longitude': -104.88622009, 'Latitude': 39.66155123},
       {'Longitude': -104.88455693, 'Latitude': 40.65079881},
       {'Longitude': -105.31427288, 'Latitude': 40.65042886},
       {'Longitude': -105.60875359, 'Latitude': 39.66001162}]}}]}}}

<span style="color: purple;">

#### STEP 3c. Use for loops to create a granule metadata GeoDataFrame. First explore the parts of the loop and then run one big loop.

</span>

In [18]:
# Break down the geometry part of the solution loop to identify the geometry of a granule
granule = wbd_hls_results[0]
# look at just the metadata, umm, of the first result
info_dict = granule['umm']
# create a list of all points, lat/lon, for the first result from the umm column of the first result
points = (
    info_dict
    # select the first thing in the GPolygons list
    ['SpatialExtent']['HorizontalSpatialDomain']['Geometry']['GPolygons'][0]
    ['Boundary']['Points'])
# create the geometry (Polygon) of the first result using Polygon from shapely
# loop through all the points in our points list and get the lat/long for each one to create the geometry
geometry = Polygon(
    [(point['Longitude'], point['Latitude']) for point in points])

print(points)
print(geometry)

[{'Longitude': -105.60875359, 'Latitude': 39.66001162}, {'Longitude': -104.88622009, 'Latitude': 39.66155123}, {'Longitude': -104.88455693, 'Latitude': 40.65079881}, {'Longitude': -105.31427288, 'Latitude': 40.65042886}, {'Longitude': -105.60875359, 'Latitude': 39.66001162}]
POLYGON ((-105.60875359 39.66001162, -104.88622009 39.66155123, -104.88455693 40.65079881, -105.31427288 40.65042886, -105.60875359 39.66001162))


In [19]:
# open test granule
opened_granule = earthaccess.open([granule])

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

In [20]:
# look at opened_granule
# 15 different .tif files, each for a different band
# All the bands for 1 granule have the same tile_id, geometry, and datetime
opened_granule

[<File-like object HTTPFileSystem, https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B04.tif>,
 <File-like object HTTPFileSystem, https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B06.tif>,
 <File-like object HTTPFileSystem, https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B02.tif>,
 <File-like object HTTPFileSystem, https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.B03.tif>,
 <File-like object HTTPFileSystem, https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T13TDE.2023121T173646.v2.0/HLS.L30.T13TDE.2023121T173646.v2.0.SAA.tif>,
 <File-like object HTTPFileSystem, https://data.lpdaac.earth

In [21]:
# What type of object is one element of the opened_granule?
type(opened_granule[0])

earthaccess.store.EarthAccessFile

In [22]:
# get tile ids and band ids for the granule
# Compile a regular expression to search for metadata
# the r indicates this is a raw string and highlights all escaped characters (the dots), limits our need to escape special characters
uri_re = re.compile(
    r"HLS\.L30\.(?P<tile_id>T[0-9A-Z]+)"
    r"\.\d+T\d+\.v\d\.\d\."
    r"(?P<band_id>[A-Za-z0-9].+)\.tif"
)

#this yields a dictionary with the tile id and band id
uri_re.search(opened_granule[0].full_name).groupdict()

{'tile_id': 'T13TDE', 'band_id': 'B04'}

In [ ]:
# Define a function to create a geodataframe with granule metadata
def create_granule_gdf(results):
    """
    Create a GeoDataFrame with HLS granule metadata: datetime, url, tile_id, band_id, and geometry.
    
    Parameters:
    results : list of HLS tiles from searching earthaccess
    
    Returns:
    file_gdf : GeoDataFrame w/ granule metadata
    """
    ## compile regular expression to search for metadata - tile_id and band_id
    url_re = re.compile(
        r'\.(?P<tile_id>\w+)\.\d+T\d+\.v\d\.\d\.(?P<band>[A-Za-z0-9]+)\.tif')

    # Loop through each granule
    # create an empty list for the metadata to be added to
    link_rows = []
    # For each granule in the HLS results...
    for granule in tqdm(results):
        # Identify granule metadata (umm column of HLS results)
        info_dict = granule['umm']
        # Identify granule datetime
        datetime = pd.to_datetime(
            info_dict
            ['TemporalExtent']['RangeDateTime']['BeginningDateTime'])
        # Identify the granule geometry by creating a list of all points,
        # lat/lon, for the first result from the umm column HLS result
        points = (
            info_dict
            # select the first thing in the GPolygons list
            ['SpatialExtent']['HorizontalSpatialDomain']['Geometry']['GPolygons'][0]
            ['Boundary']['Points'])
        # create geometry (Polygon) of the first result using Polygon from shapely
        # loop through all the points in our points list and get the lat/lon for each one to create the granule geometry
        geometry = Polygon(
            [(point['Longitude'], point['Latitude']) for point in points])
        
        # Get granule URL by opening each HLS result
        files = earthaccess.open([granule])

        # Build metadata DataFrame
        # for each URL in the files list...
        for file in files:
            # use a regular expression to search for the URL's metadata
            match = url_re.search(file.full_name)
            # if the regular expression search exists,
            if match is not None:
                # add a dictionary with the URL's metadata to the link_rows list
                link_rows.append(
                    gpd.GeoDataFrame(
                        dict(
                            datetime=[datetime],
                            tile_id=[match.group('tile_id')],
                            band=[match.group('band')],
                            url=[file],
                            geometry=[geometry]
                        ),
                        crs="EPSG:4326"
                    )
                )

    # Concatenate metadata DataFrame
    file_gdf = pd.concat(link_rows).reset_index(drop=True)
    return file_gdf

In [24]:
# use create_granule_gdf function to create a gdf with granule metadata
granule_gdf = create_granule_gdf(wbd_hls_results)

  0%|          | 0/45 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

...

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

In [25]:
# check type of granule_gdf
type(granule_gdf)

geopandas.geodataframe.GeoDataFrame

In [26]:
# Check granule_gdf
# there are 675 rows - 45 granules, 15 bands per granule
granule_gdf

datetime tile_id   band  \
0   2023-05-01 17:36:46.126000+00:00  T13TDE    B04   
1   2023-05-01 17:36:46.126000+00:00  T13TDE    B06   
2   2023-05-01 17:36:46.126000+00:00  T13TDE    B02   
3   2023-05-01 17:36:46.126000+00:00  T13TDE    B03   
4   2023-05-01 17:36:46.126000+00:00  T13TDE    SAA   
..                               ...     ...    ...   
670 2023-10-31 17:43:41.798000+00:00  T13TDE    SAA   
671 2023-10-31 17:43:41.798000+00:00  T13TDE    B05   
672 2023-10-31 17:43:41.798000+00:00  T13TDE    VAA   
673 2023-10-31 17:43:41.798000+00:00  T13TDE    B09   
674 2023-10-31 17:43:41.798000+00:00  T13TDE  Fmask   

                                                   url  \
0    <File-like object HTTPFileSystem, https://data...   
1    <File-like object HTTPFileSystem, https://data...   
2    <File-like object HTTPFileSystem, https://data...   
3    <File-like object HTTPFileSystem, https://data...   
4    <File-like object HTTPFileSystem, https://data...   
..                                                 ...   
670  <File-like object HTTPFileSystem, https://data...   
671  <File-like object HTTPFileSystem, https://data...   
672  <File-like object HTTPFileSystem, https://data...   
673  <File-like object HTTPFileSystem, https://data...   
674  <File-like object HTTPFileSystem, https://data...   

                                              geometry  
0    POLYGON ((-105.60875 39.66001, -104.88622 39.6...  
1    POLYGON ((-105.60875 39.66001, -104.88622 39.6...  
2    POLYGON ((-105.60875 39.66001, -104.88622 39.6...  
3    POLYGON ((-105.60875 39.66001, -104.88622 39.6...  
4    POLYGON ((-105.60875 39.66001, -104.88622 39.6...  
..                                                 ...  
670  POLYGON ((-106.16613 39.65575, -104.89461 39.6...  
671  POLYGON ((-106.16613 39.65575, -104.89461 39.6...  
672  POLYGON ((-106.16613 39.65575, -104.89461 39.6...  
673  POLYGON ((-106.16613 39.65575, -104.89461 39.6...  
674  POLYGON ((-106.16613 39.65575, -104.89461 39.6...  

[675 rows x 5 columns]

In [27]:
# how many tile_ids
granule_gdf.tile_id.unique()

array(['T13TDE'], dtype=object)

In [28]:
# how many geometries
granule_gdf.geometry.unique()

<GeometryArray>
[<POLYGON ((-105.609 39.66, -104.886 39.662, -104.885 40.651, -105.314 40.65,...>,
 <POLYGON ((-106.166 39.656, -104.923 39.662, -104.886 39.773, -104.885 40.65...>,
 <POLYGON ((-105.598 39.66, -104.886 39.662, -104.885 40.651, -105.304 40.65,...>,
 <POLYGON ((-106.166 39.656, -104.914 39.662, -104.886 39.746, -104.885 40.65...>,
 <POLYGON ((-105.568 39.66, -104.886 39.662, -104.885 40.651, -105.272 40.651...>,
 <POLYGON ((-106.166 39.656, -104.886 39.662, -104.885 40.651, -106.183 40.64...>,
 <POLYGON ((-105.597 39.66, -104.886 39.662, -104.885 40.651, -105.303 40.65,...>,
 <POLYGON ((-106.166 39.656, -104.926 39.662, -104.886 39.784, -104.885 40.65...>,
 <POLYGON ((-105.548 39.66, -104.886 39.662, -104.885 40.651, -105.252 40.651...>,
 <POLYGON ((-105.621 39.66, -104.886 39.662, -104.885 40.651, -105.326 40.65,...>,
 <POLYGON ((-105.552 39.66, -104.886 39.662, -104.885 40.651, -105.257 40.651...>,
 <POLYGON ((-105.559 39.66, -104.886 39.662, -104.885 40.651, -105.263 

### Open, crop, and mask data

This will be the most resource-intensive step. I recommend caching your
results using the `cached` decorator or by writing your own caching
code. I also recommend testing this step with one or two dates before
running the full computation.

This code should include at least one **function** including a
numpy-style docstring. A good place to start would be a function for
opening a single masked raster, applying the appropriate scale
parameter, and cropping.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each granule:
<ol type="1">
<li><p>Open the Fmask band, crop, and compute a quality mask for the
granule. You can use the following code as a starting point, making sure
that <code>mask_bits</code> contains the quality bits you want to
consider: ```python # Expand into a new dimension of binary bits bits =
( np.unpackbits(da.astype(np.uint8), bitorder=‘little’)
.reshape(da.shape + (-1,)) )</p>
<p># Select the required bits and check if any are flagged mask =
np.prod(bits[…, mask_bits]==0, axis=-1) ```</p></li>
<li><p>For each band that starts with ‘B’:</p>
<ol type="1">
<li>Open the band, crop, and apply the scale factor</li>
<li>Name the DataArray after the band using the <code>.name</code>
attribute</li>
<li>Apply the cloud mask using the <code>.where()</code> method</li>
<li>Store the DataArray in your data structure (e.g. adding a
GeoDataFrame column with the DataArray in it. Note that you will need to
remove the rows for unused bands)</li>
</ol></li>
</ol></li>
</ol></div></div>

<span style="color: purple;">

#### STEP 3d. Create a DataFrame with reflectance information

</span>

In [39]:
@cached('llhc_reflectance_da_df', override=True)
def compute_reflectance_da(search_results, boundary_gdf):
    """
    Connect to files over VSI, crop, cloud mask, and wrangle
    
    Returns a single reflectance DataFrame 
    with all bands as columns and
    centroid coordinates and datetime as the index.
    
    Parameters
    ==========
    file_gdf (search_results) : pd.DataFrame
        File connection and metadata (datetime, tile_id, band, and url)
    boundary_gdf : gpd.GeoDataFrame
        Boundary use to crop the data
    """
    def open_dataarray(url, boundary_proj_gdf, scale=1, masked=True):
        # Open masked DataArray
        da = rxr.open_rasterio(url, masked=masked).squeeze() * scale
        
        # Reproject site boundary if needed
        if boundary_proj_gdf is None:
            ## reproject boundary site boundary_gdf to the same crs as the search_results crs
            boundary_proj_gdf = boundary_gdf.to_crs(da.rio.crs)
            
        # Crop the DataArray with the opened urls to the reprojected site boundary
        cropped_da = da.rio.clip_box(*boundary_proj_gdf.total_bounds)
        return cropped_da
    
    def compute_quality_mask(da, mask_bits=[1, 2, 3]):
        """
        Mask out low quality data by bit
        
        Parameters
        ----------
        da : DataArray

        mask_bits : list
            bits to be masked
        
        Returns
        -------
        mask : numpy.ndarray
            quality mask
        """
        # Unpack bits into a new axis
        bits = (
            ## make each number in the dataarray binary
            np.unpackbits(
                ## change dataarray integer type to unsigned 8 bit integer type
                ## there will be 8 bits per number
                ## we do this because python will read the numbers as integers otherwise
                da.astype(np.uint8), bitorder='little'
            ).reshape(da.shape + (-1,))
        )

        # Select the required bits and check if any are flagged
        ## if the mask_bits equal 0, that means there isn't clouds, high aerosols, etc, so we only want to keep those bits.
        ## this will get rid of mask_bits that equal 1, aka where clouds, high aerosols, etc are.
        mask = np.prod(bits[..., mask_bits]==0,
                       ## add an axis so each number is converted to an array of 8 bits
                       ## each row has 1 number from original array in 8 bit format
                       axis=-1)
        return mask

    ## create a DataFrame with granule metadata
    file_gdf = create_granule_gdf(search_results)
    
    ## create empty list to gather bands that are cropped and have the cloud mask
    granule_da_rows= []
    ## set boundary_proj_gdf to None so that the site boundary_gdf gets reprojected to the same crs as the search_results crs
    boundary_proj_gdf = None

    # Loop through each image
    group_iter = file_gdf.groupby(['datetime', 'tile_id'])
    for (datetime, tile_id), granule_df in tqdm(group_iter):
        print(f'Processing granule {tile_id} {datetime}')
              
        # Open granule cloud cover
        cloud_mask_url = (
            # locate the Fmask band and corresponding url of each granule in the granule metadata DataFrame
            granule_df.loc[granule_df.band=='Fmask', 'url']
            ## remove the series wrapper of the column get the first value in the array
            .values[0])
        ## create a DataArray with the Fmask bands opened and cropped to the site bounds
        cloud_mask_cropped_da = open_dataarray(cloud_mask_url, boundary_proj_gdf, masked=False)

        # Compute cloud mask
        cloud_mask = compute_quality_mask(cloud_mask_cropped_da)

        # Loop through each spectral band
        da_list = []
        df_list = []
        for i, row in granule_df.iterrows():
            if row.band.startswith('B'):
                # Open, crop, and mask the band
                band_cropped = open_dataarray(
                    row.url, boundary_proj_gdf, scale=0.0001)
                band_cropped.name = row.band
                # Add the opened, cropped, and masked B band DataArray to the metadata DataFrame row
                ## also apply the cloud mask to the B band DataArray
                row['da'] = (band_cropped
                             ## for all the bits we don't want (clouds, cloud shadows, high aerosol, etc),
                             ## we'll have NaN values instead of the original spectral signature
                             .where(cloud_mask))
                ## add the metadata DataFrame row to the granule_da_rows list
                granule_da_rows.append(row
                                       ## first convert the row series to a DataFrame
                                       .to_frame()
                                       ## transpose the DataFrame
                                       .T)
    
    # Reassemble the metadata DataFrame
    return pd.concat(granule_da_rows)

# Use the above function to create a reflectance_da_df
llhc_reflectance_da_df = compute_reflectance_da(wbd_hls_results, wbd_gdf)

  0%|          | 0/45 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

...

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

Processing granule T13TDE 2023-05-01 17:36:46.126000+00:00
Processing granule T13TDE 2023-05-08 17:42:50.705000+00:00
Processing granule T13TDE 2023-05-09 17:36:57.025000+00:00
Processing granule T13TDE 2023-05-16 17:43:04.644000+00:00
Processing granule T13TDE 2023-05-17 17:36:33.039000+00:00
Processing granule T13TDE 2023-05-24 17:42:47.017000+00:00
Processing granule T13TDE 2023-05-25 17:36:46.460000+00:00
Processing granule T13TDE 2023-06-01 17:42:56.999000+00:00
Processing granule T13TDE 2023-06-02 17:36:37.078000+00:00
Processing granule T13TDE 2023-06-09 17:42:53.790000+00:00
Processing granule T13TDE 2023-06-10 17:36:41.386000+00:00
Processing granule T13TDE 2023-06-17 17:42:48.052000+00:00
Processing granule T13TDE 2023-06-18 17:36:46.079000+00:00
Processing granule T13TDE 2023-06-25 17:43:00.237000+00:00
Processing granule T13TDE 2023-06-26 17:36:38.725000+00:00
Processing granule T13TDE 2023-07-03 17:42:59.354000+00:00
Processing granule T13TDE 2023-07-04 17:36:56.910000+00:

In [40]:
# Check the type of the reflectance_da_df
type(llhc_reflectance_da_df)

pandas.core.frame.DataFrame

In [41]:
# Check the reflectance_da_df (this takes about a minute)
llhc_reflectance_da_df.head(3)

datetime tile_id band  \
0  2023-05-01 17:36:46.126000+00:00  T13TDE  B04   
1  2023-05-01 17:36:46.126000+00:00  T13TDE  B06   
2  2023-05-01 17:36:46.126000+00:00  T13TDE  B02   

                                                 url  \
0  <File-like object HTTPFileSystem, https://data...   
1  <File-like object HTTPFileSystem, https://data...   
2  <File-like object HTTPFileSystem, https://data...   

                                            geometry  \
0  POLYGON ((-105.60875359 39.66001162, -104.8862...   
1  POLYGON ((-105.60875359 39.66001162, -104.8862...   
2  POLYGON ((-105.60875359 39.66001162, -104.8862...   

                                                  da  
0  [[<xarray.DataArray 'B04' ()> Size: 4B\narray(...  
1  [[<xarray.DataArray 'B06' ()> Size: 4B\narray(...  
2  [[<xarray.DataArray 'B02' ()> Size: 4B\narray(...

In [56]:
# look at dataarray for first row
llhc_reflectance_da_df.loc[0].da

<xarray.DataArray 'B04' (y: 241, x: 604)> Size: 582kB
array([[       nan,        nan,        nan, ...,        nan,        nan,
               nan],
       [       nan,        nan,        nan, ...,        nan,        nan,
               nan],
       [       nan,        nan,        nan, ...,        nan,        nan,
               nan],
       ...,
       [0.0964    , 0.0954    , 0.0937    , ..., 0.081     , 0.0625    ,
        0.063     ],
       [0.0986    , 0.0962    , 0.0955    , ..., 0.0836    , 0.0676    ,
        0.0584    ],
       [0.1071    , 0.0986    , 0.09559999, ...,        nan,        nan,
               nan]], dtype=float32)
Coordinates:
    band         int64 8B 1
  * x            (x) float64 5kB 4.745e+05 4.745e+05 ... 4.925e+05 4.926e+05
  * y            (y) float64 2kB 4.445e+06 4.445e+06 ... 4.438e+06 4.438e+06
    spatial_ref  int64 8B 0

### Merge and Composite Data

You will notice for this watershed that: 1. The raster data for each
date are spread across 4 granules 2. Any given image is incomplete
because of clouds

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li><p>For each band:</p>
<ol type="1">
<li><p>For each date:</p>
<ol type="1">
<li>Merge all 4 granules</li>
<li>Mask any negative values created by interpolating from the nodata
value of -9999 (<code>rioxarray</code> should account for this, but
doesn’t appear to when merging. If you leave these values in they will
create problems down the line)</li>
</ol></li>
<li><p>Concatenate the merged DataArrays along a new date
dimension</p></li>
<li><p>Take the mean in the date dimension to create a composite image
that fills cloud gaps</p></li>
<li><p>Add the band as a dimension, and give the DataArray a
name</p></li>
</ol></li>
<li><p>Concatenate along the band dimension</p></li>
</ol></div></div>

<span style="color: purple;">

#### STEP 3e. Explore llhc_reflectance_da_df

</span>

In [42]:
## how many unique datetimes are there in the llhc_reflectance_da_df datetime column?
llhc_reflectance_da_df.datetime.unique()

array([Timestamp('2023-05-01 17:36:46.126000+0000', tz='UTC'),
       Timestamp('2023-05-08 17:42:50.705000+0000', tz='UTC'),
       Timestamp('2023-05-09 17:36:57.025000+0000', tz='UTC'),
       Timestamp('2023-05-16 17:43:04.644000+0000', tz='UTC'),
       Timestamp('2023-05-17 17:36:33.039000+0000', tz='UTC'),
       Timestamp('2023-05-24 17:42:47.017000+0000', tz='UTC'),
       Timestamp('2023-05-25 17:36:46.460000+0000', tz='UTC'),
       Timestamp('2023-06-01 17:42:56.999000+0000', tz='UTC'),
       Timestamp('2023-06-02 17:36:37.078000+0000', tz='UTC'),
       Timestamp('2023-06-09 17:42:53.790000+0000', tz='UTC'),
       Timestamp('2023-06-10 17:36:41.386000+0000', tz='UTC'),
       Timestamp('2023-06-17 17:42:48.052000+0000', tz='UTC'),
       Timestamp('2023-06-18 17:36:46.079000+0000', tz='UTC'),
       Timestamp('2023-06-25 17:43:00.237000+0000', tz='UTC'),
       Timestamp('2023-06-26 17:36:38.725000+0000', tz='UTC'),
       Timestamp('2023-07-03 17:42:59.354000+0000', tz=

In [43]:
## what is the name of the dataarray in the 0 index of the llhc_reflectance_da_df?
llhc_reflectance_da_df.loc[0].da.name

'B04'

In [44]:
## how many unique tile_ids are there in the llhc_reflectance_da_df datetime column?
llhc_reflectance_da_df.tile_id.unique()

array(['T13TDE'], dtype=object)

<span style="color: purple;">

#### STEP 3f. Merge and composite granules of llhc_reflectance_da_df

</span>

In [45]:
@cached('llhc_reflectance_da')
def merge_and_composite_arrays(granule_da_df):
    # Merge and composite an image for each band
    df_list = []
    da_list = []
    for band, band_df in tqdm(granule_da_df.groupby('band')):
        merged_das = []
        for datetime, date_df in tqdm(band_df.groupby('datetime')):
            # Merge granules for each date
            merged_da = rxrmerge.merge_arrays(list(date_df.da))
            # Mask negative values
            merged_da = merged_da.where(merged_da>0)
            ## add merged dataarrays w/ negative values masked to the merged_das list
            merged_das.append(merged_da)
            
        # Composite images across dates
        ## concatenate merged dataarrays along the datetime dimension and
        ## reduce the dataarray's data by finding the median datetime
        composite_da = xr.concat(merged_das, dim='datetime').median('datetime')
        ## add a column to the composite_da called band
        composite_da['band'] = (
            ## [1:] will just look at elements from index 1 to the end (ignores index 0),
            ## int converts the value to an integer
            int(band[1:]))
        ## the name of the composite dataarray will be reflectance
        composite_da.name = 'reflectance'
        ## add the composite_da to the da_list
        da_list.append(composite_da)
        
    return xr.concat(da_list, dim='band')

llhc_reflectance_da = merge_and_composite_arrays(llhc_reflectance_da_df)
llhc_reflectance_da

  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

...

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

  0%|          | 0/45 [00:00<?, ?it/s]

<xarray.DataArray 'reflectance' (band: 10, y: 241, x: 604)> Size: 6MB
array([[[0.0413    , 0.0386    , 0.03845   , ..., 0.0379    ,
         0.0351    , 0.0356    ],
        [0.04015   , 0.04445   , 0.03975   , ..., 0.0331    ,
         0.0334    , 0.0471    ],
        [0.0391    , 0.0467    , 0.04095   , ..., 0.038     ,
         0.0476    , 0.0551    ],
        ...,
        [0.0333    , 0.032     , 0.0367    , ..., 0.02555   ,
         0.0144    , 0.0165    ],
        [0.0328    , 0.031     , 0.0371    , ..., 0.02665   ,
         0.0162    , 0.01725   ],
        [0.0353    , 0.034     , 0.0348    , ..., 0.0264    ,
         0.0162    , 0.0166    ]],

       [[0.04525   , 0.0439    , 0.0455    , ..., 0.0412    ,
         0.0405    , 0.0381    ],
        [0.04775   , 0.0533    , 0.0485    , ..., 0.0371    ,
         0.0418    , 0.0531    ],
        [0.04695   , 0.05545   , 0.0497    , ..., 0.0407    ,
         0.0565    , 0.065     ],
...
        [0.2471    , 0.2562    , 0.2669    , ..., 0.23345   ,
         0.22649999, 0.2163    ],
        [0.24749999, 0.25579998, 0.2665    , ..., 0.23519999,
         0.22854999, 0.21845   ],
        [0.2481    , 0.255     , 0.2653    , ..., 0.2377    ,
         0.2314    , 0.2215    ]],

       [[0.25945002, 0.25575   , 0.25379997, ..., 0.25329998,
         0.2536    , 0.2541    ],
        [0.2597    , 0.2564    , 0.25475   , ..., 0.2564    ,
         0.2568    , 0.2582    ],
        [0.25965   , 0.2575    , 0.2562    , ..., 0.25605   ,
         0.2592    , 0.26479998],
        ...,
        [0.2385    , 0.2471    , 0.2545    , ..., 0.22534999,
         0.2193    , 0.21085   ],
        [0.2394    , 0.24599999, 0.25169998, ..., 0.2283    ,
         0.2211    , 0.2119    ],
        [0.239     , 0.24399999, 0.2507    , ..., 0.2314    ,
         0.2253    , 0.2121    ]]], dtype=float32)
Coordinates:
  * x            (x) float64 5kB 4.745e+05 4.745e+05 ... 4.925e+05 4.926e+05
  * y            (y) float64 2kB 4.445e+06 4.445e+06 ... 4.438e+06 4.438e+06
  * band         (band) int64 80B 1 2 3 4 5 6 7 9 10 11
    spatial_ref  int64 8B 0

llhc_reflectance_da hs 3 dimensions: band (10 spectral bands from HLS data), x, and y.

HLS UserGuide tells us the units and scale of each band (among other things). All bands except 10 and 11 have units of reflectance and a scale value of 0.0001. Bands 10 and 11 have units of degrees Celsius and scales of 0.01. Bands 10 and 11 are thermal bands. If we were to include bands 10 and 11 in our k-means clustering, we would need to change the scale to 0.0001. We'll drop bands 10 and 11 in this case since they're thermal bands.

Reflectance units are values between 0 and 1 that tells us what fraction of light is being reflected back to us.

## STEP 4: K-MEANS

Cluster your data by spectral signature using the k-means algorithm.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Convert your DataArray into a <strong>tidy</strong> DataFrame of
reflectance values (hint: check out the <code>.to_dataframe()</code> and
<code>.unstack()</code> methods)</li>
<li>Filter out all rows with no data (all 0s or any N/A values)</li>
<li>Fit a k-means model. You can experiment with the number of groups to
find what works best.</li>
</ol></div></div>

<span style="color: purple;">

#### STEP 4a. Convert spectral DataArray to DataFrame

</span>

In [77]:
# Create a column for each of the bands
# yeilds a DataFrame with a column for each band and x and y columns (location of pixels)
model_df = (llhc_reflectance_da.to_dataframe()
            # unstack reflectance bands so they each get their own column
            .reflectance.unstack('band'))
model_df

band                     1        2        3        4        5        6   \
y         x                                                                
4444965.0 474465.0  0.04130  0.04525  0.06875  0.07230  0.22185  0.21430   
          474495.0  0.03860  0.04390  0.06850  0.07270  0.22485  0.21375   
          474525.0  0.03845  0.04550  0.07170  0.07865  0.22410  0.21320   
          474555.0  0.04225  0.04900  0.07680  0.08520  0.20365  0.19865   
          474585.0  0.04440  0.05110  0.07725  0.09610  0.19590  0.19575   
...                     ...      ...      ...      ...      ...      ...   
4437765.0 492435.0  0.05400  0.06270  0.09820  0.10740  0.30300  0.26480   
          492465.0  0.04510  0.05610  0.08960  0.10460  0.28280  0.26100   
          492495.0  0.02640  0.03490  0.06180  0.06370  0.27890  0.18540   
          492525.0  0.01620  0.02040  0.04390  0.03680  0.24590  0.11870   
          492555.0  0.01660  0.02210  0.04460  0.03470  0.19450  0.09020   

band                     7        9        10       11  
y         x                                             
4444965.0 474465.0  0.14175  0.00125  0.27240  0.25945  
          474495.0  0.13855  0.00120  0.27025  0.25575  
          474525.0  0.13950  0.00110  0.26820  0.25380  
          474555.0  0.13880  0.00120  0.26635  0.25340  
          474585.0  0.15150  0.00125  0.26570  0.25385  
...                     ...      ...      ...      ...  
4437765.0 492435.0  0.17270  0.00150  0.24130  0.23290  
          492465.0  0.16080  0.00140  0.24090  0.23330  
          492495.0  0.10640  0.00140  0.23770  0.23140  
          492525.0  0.05440  0.00130  0.23140  0.22530  
          492555.0  0.04810  0.00130  0.22150  0.21210  

[145564 rows x 10 columns]

In [78]:
# drop bands 10 and 11 since they're thermal bands and any rows w/ NaN values
model_df = model_df.drop(columns = [10, 11]).dropna()
model_df

band                      1        2        3        4        5        6  \
y         x                                                                
4444965.0 474465.0  0.04130  0.04525  0.06875  0.07230  0.22185  0.21430   
          474495.0  0.03860  0.04390  0.06850  0.07270  0.22485  0.21375   
          474525.0  0.03845  0.04550  0.07170  0.07865  0.22410  0.21320   
          474555.0  0.04225  0.04900  0.07680  0.08520  0.20365  0.19865   
          474585.0  0.04440  0.05110  0.07725  0.09610  0.19590  0.19575   
...                     ...      ...      ...      ...      ...      ...   
4437765.0 492435.0  0.05400  0.06270  0.09820  0.10740  0.30300  0.26480   
          492465.0  0.04510  0.05610  0.08960  0.10460  0.28280  0.26100   
          492495.0  0.02640  0.03490  0.06180  0.06370  0.27890  0.18540   
          492525.0  0.01620  0.02040  0.04390  0.03680  0.24590  0.11870   
          492555.0  0.01660  0.02210  0.04460  0.03470  0.19450  0.09020   

band                      7        9  
y         x                           
4444965.0 474465.0  0.14175  0.00125  
          474495.0  0.13855  0.00120  
          474525.0  0.13950  0.00110  
          474555.0  0.13880  0.00120  
          474585.0  0.15150  0.00125  
...                     ...      ...  
4437765.0 492435.0  0.17270  0.00150  
          492465.0  0.16080  0.00140  
          492495.0  0.10640  0.00140  
          492525.0  0.05440  0.00130  
          492555.0  0.04810  0.00130  

[145564 rows x 8 columns]

In [48]:
# Check that the reflectance value ranges for each band
# make sense (should be from 0-1) by checking min and max values
min_values = model_df.min()
max_values = model_df.max()
print(min_values)
print(max_values)

band
1    0.00350
2    0.00585
3    0.00995
4    0.00360
5    0.00020
6    0.00080
7    0.00105
9    0.00100
dtype: float32
band
1    0.60780
2    0.66950
3    0.75960
4    0.81910
5    0.86535
6    0.76720
7    0.81810
9    0.00190
dtype: float32


<span style="color: purple;">

#### STEP 4b. Execute k-means algorithm

</span>

In [79]:
# Initialize k means model
k_means = KMeans(n_clusters = 5)

# Fit model and predict
# Running the fit and predict functions at the same time.
# We can do this since we don't have target data.
prediction = k_means.fit_predict(model_df.values)

# Add cluster labels to model_df as a column
# Add the predicted values back to the model DataFrame
model_df['clusters_5'] = prediction

# check new model_df
model_df

band                      1        2        3        4        5        6  \
y         x                                                                
4444965.0 474465.0  0.04130  0.04525  0.06875  0.07230  0.22185  0.21430   
          474495.0  0.03860  0.04390  0.06850  0.07270  0.22485  0.21375   
          474525.0  0.03845  0.04550  0.07170  0.07865  0.22410  0.21320   
          474555.0  0.04225  0.04900  0.07680  0.08520  0.20365  0.19865   
          474585.0  0.04440  0.05110  0.07725  0.09610  0.19590  0.19575   
...                     ...      ...      ...      ...      ...      ...   
4437765.0 492435.0  0.05400  0.06270  0.09820  0.10740  0.30300  0.26480   
          492465.0  0.04510  0.05610  0.08960  0.10460  0.28280  0.26100   
          492495.0  0.02640  0.03490  0.06180  0.06370  0.27890  0.18540   
          492525.0  0.01620  0.02040  0.04390  0.03680  0.24590  0.11870   
          492555.0  0.01660  0.02210  0.04460  0.03470  0.19450  0.09020   

band                      7        9  clusters_5  
y         x                                       
4444965.0 474465.0  0.14175  0.00125           2  
          474495.0  0.13855  0.00120           2  
          474525.0  0.13950  0.00110           2  
          474555.0  0.13880  0.00120           2  
          474585.0  0.15150  0.00125           2  
...                     ...      ...         ...  
4437765.0 492435.0  0.17270  0.00150           1  
          492465.0  0.16080  0.00140           1  
          492495.0  0.10640  0.00140           2  
          492525.0  0.05440  0.00130           2  
          492555.0  0.04810  0.00130           4  

[145564 rows x 9 columns]

In [80]:
# Initialize k means model with 4 clusters
k_means_4 = KMeans(n_clusters = 4)

# Fit model and predict
# Running the fit and predict functions at the same time.
# We can do this since we don't have target data.
prediction_4 = k_means_4.fit_predict(model_df.values)

# Add cluster labels to model_df as a column
# Add the predicted values back to the model DataFrame
model_df['clusters_4'] = prediction_4

# Initialize k means model with 3 clusters
k_means_3 = KMeans(n_clusters = 3)

# Fit model and predict
# Running the fit and predict functions at the same time.
# We can do this since we don't have target data.
prediction_3 = k_means_3.fit_predict(model_df.values)

# Add cluster labels to model_df as a column
# Add the predicted values back to the model DataFrame
model_df['clusters_3'] = prediction_3

# check new model_df
model_df

band                      1        2        3        4        5        6  \
y         x                                                                
4444965.0 474465.0  0.04130  0.04525  0.06875  0.07230  0.22185  0.21430   
          474495.0  0.03860  0.04390  0.06850  0.07270  0.22485  0.21375   
          474525.0  0.03845  0.04550  0.07170  0.07865  0.22410  0.21320   
          474555.0  0.04225  0.04900  0.07680  0.08520  0.20365  0.19865   
          474585.0  0.04440  0.05110  0.07725  0.09610  0.19590  0.19575   
...                     ...      ...      ...      ...      ...      ...   
4437765.0 492435.0  0.05400  0.06270  0.09820  0.10740  0.30300  0.26480   
          492465.0  0.04510  0.05610  0.08960  0.10460  0.28280  0.26100   
          492495.0  0.02640  0.03490  0.06180  0.06370  0.27890  0.18540   
          492525.0  0.01620  0.02040  0.04390  0.03680  0.24590  0.11870   
          492555.0  0.01660  0.02210  0.04460  0.03470  0.19450  0.09020   

band                      7        9  clusters_5  clusters_4  clusters_3  
y         x                                                               
4444965.0 474465.0  0.14175  0.00125           2           1           0  
          474495.0  0.13855  0.00120           2           1           0  
          474525.0  0.13950  0.00110           2           1           0  
          474555.0  0.13880  0.00120           2           1           0  
          474585.0  0.15150  0.00125           2           1           0  
...                     ...      ...         ...         ...         ...  
4437765.0 492435.0  0.17270  0.00150           1           2           2  
          492465.0  0.16080  0.00140           1           2           2  
          492495.0  0.10640  0.00140           2           1           0  
          492525.0  0.05440  0.00130           2           1           0  
          492555.0  0.04810  0.00130           4           3           0  

[145564 rows x 11 columns]

## STEP 5: PLOT

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><p>Create a plot that shows the k-means clusters next to an RGB image of
the area. You may need to brighten your RGB image by multiplying it by
10. The code for reshaping and plotting the clusters is provided for you
below, but you will have to create the RGB plot yourself!</p>
<p>So, what is <code>.sortby(['x', 'y'])</code> doing for us? Try the
code without it and find out.</p></div></div>

RGB Image (Red-Green-Blue Image): combine multispectral data for just the visual spectrum by stacking the red, green, and blue bands

To make RGB plot:

1. Make DataArray w/ red (B04), green (B03), and blue (B02) bands

<span style="color: purple;">

#### STEP 5a. Create RGB plot using llhc_reflectance_da

</span>

In [50]:
# make dataarray w/ bands to use for rgb plot
rgb = llhc_reflectance_da.sel(band=[4, 3, 2])

# hvplot has a rgb plot method. this will not give us a helpful plot b/c the values aren't what the rgb plot expects.
# the plot created by this is very dark b/c the numbers aren't in the right format.
# rgb plot method expects numbers to be pixel values, not integers.
(
    rgb.hvplot.rgb(
        # set the spatial components of how the pixels will be plotted
        y = 'y',
        x = 'x',
        bands = 'band',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None)
               )

:RGB   [x,y]   (R,G,B)

In [51]:
# For the rgb plot method, we want image pixel values to range from 0-255
# Then convert to unsigned 8-bit integers (data type for images)
# don't include nan values in calculation
# This still yields a very dark plot
rgb_uint8 = ((
    # multiply all values in rgb dataarray by 255
    rgb * 255)
    # convert the type of the number to unsigned 8-bit integers
    .astype(np.uint8)
    # drop nan values, don't use them in the calculation
    .where(rgb!=np.nan))


# check plot of rgb_uint8
(
    rgb_uint8.hvplot.rgb(
        # set the spatial components of how the pixels will be plotted
        y = 'y',
        x = 'x',
        bands = 'band',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None)
               )

:RGB   [x,y]   (R,G,B)

In [52]:
# We can increase the brightness of the image by multiplying all numbers by 10
# Even though we're changing the pixel values, it's just for display purposes so it's ok
# After plotting this we may get an error that the data values are too high.
rgb_uint8_bright = (rgb_uint8 * 10)

# check plot of rgb_uint8_bright
(
    rgb_uint8_bright.hvplot.rgb(
        # set the spatial components of how the pixels will be plotted
        y = 'y',
        x = 'x',
        bands = 'band',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None)
               )

:RGB   [x,y]   (R,G,B)

In [53]:
# To fix the error, cap all pixel values at 255
# If value is 255 or less than 255, keep that value.
# if value is greater than 255, replace w/ 255
rgb_sat = (rgb_uint8_bright
           .where(rgb_uint8_bright < 255, 255))

# check plot of rgb_sat
(
    rgb_sat.hvplot.rgb(
        # set the spatial components of how the pixels will be plotted
        y = 'y',
        x = 'x',
        bands = 'band',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None)
               )

:RGB   [x,y]   (R,G,B)

<span style="color: purple;">

#### STEP 5b. Create a plot of the RGB plot and k-means plot

</span>

In [90]:
# Plot the k-means clusters and rgb_sat plots next to each other
hv.Layout(
    rgb_sat.hvplot.rgb(
        # set the spatial components of how the pixels will be plotted
        y = 'y',
        x = 'x',
        bands = 'band',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None,
        title = 'RGB Plot of the Lower Left Hand Creek Watershed in Colorado',
        frame_width = 600)
    +
    (model_df.clusters_5
        # making it into an xarray
        .to_xarray()
        # making model_df.clusters into an xarray is causing important
        # spatial info to be lost. use sortby('x', 'y') to fix that.
        # w/o .sortby('x', 'y'), this plot is flipped compared to the rgb plot
        .sortby('x', 'y')
        .hvplot(
            x = 'x', y = 'y',
            # tell the plot that one unit vertically is the same as one unit horizontally
            data_aspect = 1,
            # drop axes
            xaxis = None, yaxis = None,
            # adjust coloring to a categorical color scheme
            cmap = 'Colorblind',
            title = 'Plot of K-means Clusters of Lower Left Hand Creek Watershed in Colorado (5 clusters)',
            frame_width = 600
        ))
    +
    (model_df.clusters_4
    # making it into an xarray
    .to_xarray()
    # making model_df.clusters into an xarray is causing important
    # spatial info to be lost. use sortby('x', 'y') to fix that.
    # w/o .sortby('x', 'y'), this plot is flipped compared to the rgb plot
    .sortby('x', 'y')
    .hvplot(
        x = 'x', y = 'y',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None,
        # adjust coloring to a categorical color scheme
        cmap = 'Colorblind',
        title = 'Plot of K-means Clusters of Lower Left Hand Creek Watershed in Colorado (4 clusters)',
        frame_width = 600
    ))
    +
    (model_df.clusters_3
    # making it into an xarray
    .to_xarray()
    # making model_df.clusters into an xarray is causing important
    # spatial info to be lost. use sortby('x', 'y') to fix that.
    # w/o .sortby('x', 'y'), this plot is flipped compared to the rgb plot
    .sortby('x', 'y')
    .hvplot(
        x = 'x', y = 'y',
        # tell the plot that one unit vertically is the same as one unit horizontally
        data_aspect = 1,
        # drop axes
        xaxis = None, yaxis = None,
        # adjust coloring to a categorical color scheme
        cmap = 'Colorblind',
        title = 'Plot of K-means Clusters of Lower Left Hand Creek Watershed in Colorado (3 clusters)',
        frame_width = 600
    ))
).cols(2)


:Layout
   .RGB.I     :RGB   [x,y]   (R,G,B)
   .Image.I   :Image   [x,y]   (clusters_5)
   .Image.II  :Image   [x,y]   (clusters_4)
   .Image.III :Image   [x,y]   (clusters_3)

**Plot Headline & Description:**
The K-means algorithm does a decent job on classifying different land cover types in the Lower Left Hand Creek Watershed in Boulder County, Colorado. In the 5 cluster plot above, we can generally see that different clusters correlate with different types of land cover shown in the RGB plot. For example, there are buildings from neighborhoods identified with pink in the northeast corner of the plot 5 cluster plot and we can see those buildings in the northeast corner of the RGB plot. Also, in the 5 cluster plot, the black areas indicate bodies of water that are also seen in the RGB plot. Many of those water bodies are also shown in black in the 4 cluster plot, however they aren't identifiable in the 3 cluster plot. Also, the yellow areas in the 5 cluster plot seem to correlate pretty well with the brown and yellow areas in the RGB plot. 

If I were to do this analysis again, I would do a principal components analysis and/or find the silhouette scores for different amounts of clusters. In this analysis, I manually ran the k-means algorithm with 3 and 4 clusters and by comparing the plots, it looked like 5 clusters picked up on a decent amount of land cover variation in the watershed without picking up on too much. However, it'd be nice to have actual silhouette scores to decide with. 